## Load pretrained models or train from scratch?

In [25]:
import os
import pickle
use_pickled = input("Load pickled files/models? (y/n, defaults to y): ")
if use_pickled == 'n':
    use_pickled = False
else:
    use_pickled = True

pickled_dir = "pickled"


## Load the IMDB movie review dataset
This dataset is already separated into 25,000 negative and 25,000 positive reviews for a total of 50,000 reviews.

In [2]:
import pandas as pd

data = pd.read_csv('IMDB-Dataset.csv', error_bad_lines=False);

# split positive and negative sentiment reviews
pos_reviews = data[data.sentiment == "positive"]
neg_reviews = data[data.sentiment == "negative"]

pos_data = pos_reviews[['review']]
pos_data['index'] = pos_data.index
pos_documents = pos_data

neg_data = neg_reviews[['review']]
neg_data['index'] = neg_data.index
neg_documents = neg_data

# showing that the reviews were correctly split by sentiment
print(len(pos_documents))
print(pos_documents[:5])
print(len(neg_documents))
print(neg_documents[:5])

25000
                                              review  index
0  One of the other reviewers has mentioned that ...      0
1  A wonderful little production. <br /><br />The...      1
2  I thought this was a wonderful way to spend ti...      2
4  Petter Mattei's "Love in the Time of Money" is...      4
5  Probably my all-time favorite movie, a story o...      5
25000
                                               review  index
3   Basically there's a family where a little boy ...      3
7   This show was an amazing, fresh & innovative i...      7
8   Encouraged by the positive comments about this...      8
10  Phil the Alien is one of those quirky films wh...     10
11  I saw this movie when I was about 12 when it c...     11


## Initial Preprocessing: remove punctuation and convert everything to lowercase

In [3]:
# from nltk.corpus import stopwords
import re

# stop_words = list(set(stopwords.words('english')))

'''Positive Data'''
# Remove punctuation using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
pos_documents['review_processed'] = pos_documents['review'].map(lambda x: x.lower())
'''Negative Data'''
# Remove punctuation using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: re.sub('[,\.!?]', '', x))
# Lowercase the words using regular expresssion
neg_documents['review_processed'] = neg_documents['review'].map(lambda x: x.lower())

## Generate World Cloud

Either loads the pickled objects from disk, or genereate a new word cloud objects and save it to disk.

In [4]:
from wordcloud import WordCloud

# load from pickled/wordcloud_pos and pickled/worldcloud_neg
if use_pickled:
    with open(os.path.join(pickled_dir, "wordcloud_pos"), 'rb') as f:
        wordcloud_pos = pickle.load(f)
    with open(os.path.join(pickled_dir, "wordcloud_neg"), 'rb') as f:
        wordcloud_neg = pickle.load(f)
else:
    # create a new wordcloud object for positive reviews, then write it to disk
    long_string_pos = " ".join(pos_documents.review_processed)
    wordcloud_pos = WordCloud().generate(long_string_pos)
    with open(os.path.join(pickled_dir, "wordcloud_pos"), 'wb+') as f:
        pickle.dump(wordcloud_pos, f)
    
    # create a new wordcloud object for negative reviews, then write it to disk
    long_string_neg = " ".join(neg_documents.review_processed)
    wordcloud_neg = WordCloud().generate(long_string_neg)
    with open(os.path.join(pickled_dir, "wordcloud_neg"), 'wb+') as f:
        pickle.dump(wordcloud_neg, f)

## Postitive Word Cloud

In [5]:
image = wordcloud_pos.to_image()
image.show()


## Negative Word Cloud

In [6]:
image = wordcloud_neg.to_image()
image.show()

## Stemming and Lematizing

## Lemmataizing and Stemming

In [24]:
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS
from nltk.stem import WordNetLemmatizer, SnowballStemmer
from nltk.stem.porter import *
import numpy as np
np.random.seed(2018)
import nltk

stemmer = SnowballStemmer("english")
def lemmatize_stemming(text):
    return stemmer.stem(WordNetLemmatizer().lemmatize(text, pos='v'))


def preprocess(text):
    result = []
    for token in gensim.utils.simple_preprocess(text):
        if token not in gensim.parsing.preprocessing.STOPWORDS and len(token) > 3:
            result.append(lemmatize_stemming(token))
    return result

pos_proc_docs_fname = os.path.join(pickled_dir, "pos_processed_docs")
neg_proc_docs_fname = os.path.join(pickled_dir, "neg_processed_docs")
if use_pickled:
    with open(pos_proc_docs_fname, 'rb') as f1:
        pos_processed_documents = pickle.load(f1)
    with open(neg_proc_docs_fname, 'rb') as f2:
        neg_processed_documents = pickle.load(f2)
else:
    pos_processed_documents = pos_documents['review_processed'].map(preprocess)
    neg_processed_documents = neg_documents['review_processed'].map(preprocess)
    with open(pos_proc_docs_fname, 'wb+') as f1:
        pickle.dump(pos_processed_documents, f1)
    with open(neg_proc_docs_fname, 'wb+') as f2:
        pickle.dump(neg_processed_documents, f2)

print("Positive reviews after lemmatizing and stemming:")
print(len(pos_processed_documents))
print(pos_processed_documents[:10])

print("\nNegative reviews after lemmatizing and stemming:")
print(len(neg_processed_documents))
print(neg_processed_documents[:10])

Positive reviews after lemmatizing and stemming:


TypeError: object of type 'WordCloud' has no len()

In [9]:
# Making Positive and Negative Dictionaries
pos_dictionary = gensim.corpora.Dictionary(pos_processed_documents)
count = 0
print("\nSome random positive words in our dictionary: ")
for k, v in pos_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break    
neg_dictionary = gensim.corpora.Dictionary(neg_processed_documents)
count = 0
print("\nSome random negative words in our dictionary: ")
for k, v in neg_dictionary.iteritems():
    print(k, v)
    count += 1
    if count > 10:
        break


Some random positive words in our dictionary: 
0 accustom
1 agenda
2 agreement
3 appeal
4 aryan
5 audienc
6 away
7 bitch
8 brutal
9 call
10 cell

Some random negative words in our dictionary: 
0 argu
1 basic
2 boogeyman
3 closet
4 decid
5 descent
6 dialog
7 divorc
8 drama
9 expect
10 famili


In [10]:
# Making Postiive and Negative LDA Models
pos_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
pos_bow_corpus = [pos_dictionary.doc2bow(doc) for doc in pos_processed_documents]
pos_lda_model = gensim.models.LdaMulticore(pos_bow_corpus, num_topics=150, id2word=pos_dictionary, passes=10, workers=2)

neg_dictionary.filter_extremes(no_below=15, no_above=0.5, keep_n=100000)
neg_bow_corpus = [neg_dictionary.doc2bow(doc) for doc in neg_processed_documents]
neg_lda_model = gensim.models.LdaMulticore(neg_bow_corpus, num_topics=150, id2word=neg_dictionary, passes=10, workers=2)

In [11]:
# Viewing the LDA Model Topic Results
print("\nFirst Ten Positive Review Topics:")
for idx, topic in pos_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break
print("\nFirst Ten Negative Review Topics")
for idx, topic in neg_lda_model.print_topics(-1):
    print('Topic: {} \nWords: {}'.format(idx, topic))
    if idx>=9:
        break


First Ten Positive Review Topics:
Topic: 0 
Words: 0.032*"team" + 0.019*"like" + 0.019*"play" + 0.018*"sport" + 0.017*"role" + 0.017*"footbal" + 0.015*"actor" + 0.013*"basebal" + 0.012*"great" + 0.012*"good"
Topic: 1 
Words: 0.018*"urban" + 0.013*"charact" + 0.012*"luci" + 0.011*"virgin" + 0.010*"earli" + 0.010*"right" + 0.009*"play" + 0.009*"offens" + 0.008*"style" + 0.008*"like"
Topic: 2 
Words: 0.022*"charact" + 0.013*"scene" + 0.010*"work" + 0.008*"director" + 0.007*"stori" + 0.007*"make" + 0.007*"point" + 0.006*"perform" + 0.005*"effect" + 0.005*"emot"
Topic: 3 
Words: 0.079*"releas" + 0.053*"comment" + 0.049*"christma" + 0.018*"review" + 0.017*"spanish" + 0.017*"print" + 0.015*"holiday" + 0.014*"see" + 0.014*"titl" + 0.014*"classic"
Topic: 4 
Words: 0.024*"play" + 0.023*"richard" + 0.020*"jean" + 0.018*"role" + 0.017*"joan" + 0.016*"cagney" + 0.013*"gangster" + 0.013*"warner" + 0.011*"star" + 0.010*"bull"
Topic: 5 
Words: 0.038*"king" + 0.028*"british" + 0.017*"media" + 0.015*"g

In [12]:
from gensim.models import CoherenceModel

# Compute Perplexity
print('\nPositive Perplexity: ', pos_lda_model.log_perplexity(pos_bow_corpus))  # a measure of how good the model is. lower the better.
# Compute Coherence Score
pos_coherence_model_lda = CoherenceModel(model=pos_lda_model, texts=pos_processed_documents, dictionary=pos_dictionary, coherence='c_v')
pos_coherence_lda = pos_coherence_model_lda.get_coherence()
print('Positive Coherence Score: ', pos_coherence_lda)
'''Negative Topics'''
# Compute Perplexity
print('\nNegative Perplexity: ', neg_lda_model.log_perplexity(neg_bow_corpus))  # a measure of how good the model is. lower the better.
# Compute Coherence Score
neg_coherence_model_lda = CoherenceModel(model=neg_lda_model, texts=neg_processed_documents, dictionary=neg_dictionary, coherence='c_v')
neg_coherence_lda = neg_coherence_model_lda.get_coherence()
print('Negative Coherence Score: ', neg_coherence_lda)


Positive Perplexity:  -8.092771066060543
Positive Coherence Score:  0.31947427660032335

Negative Perplexity:  -8.165978130504575
Negative Coherence Score:  0.3061946201591925


In [13]:
#import gensim

#'''Positive'''
# Download File: http://mallet.cs.umass.edu/dist/mallet-2.0.8.zip
#mallet_path = r'C:/MALLET/bin/mallet.bat' # update this path
#pos_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=pos_bow_corpus, num_topics=30, id2word=pos_dictionary)

# Show Topics
#print(pos_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#pos_coherence_model_ldamallet = CoherenceModel(model=pos_ldamallet, texts=pos_processed, dictionary=pos_dictionary, coherence='c_v')
#pos_coherence_ldamallet = pos_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', pos_coherence_ldamallet)

#'''Negative'''
#neg_ldamallet = gensim.models.wrappers.LdaMallet(mallet_path, corpus=neg_bow_corpus, num_topics=30, id2word=neg_dictionary)

# Show Topics
#print(neg_ldamallet.show_topics(formatted=False))
# Compute Coherence Score
#neg_coherence_model_ldamallet = CoherenceModel(model=neg_ldamallet, texts=neg_processed, dictionary=neg_dictionary, coherence='c_v')
#neg_coherence_ldamallet = neg_coherence_model_ldamallet.get_coherence()
#print('\nCoherence Score: ', neg_coherence_ldamallet)

In [14]:
import pyLDAvis
import pyLDAvis.gensim

# Visualize positive topic words
pyLDAvis.enable_notebook()
pos_vis = pyLDAvis.gensim.prepare(pos_lda_model, pos_bow_corpus, pos_dictionary)
pos_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
111    0.215810 -0.013420       1        1  5.363122
2      0.096214  0.043327       2        1  3.915700
112    0.183936 -0.170158       3        1  3.776103
109    0.173094 -0.069792       4        1  3.071983
58     0.132686  0.196832       5        1  2.645726
...         ...       ...     ...      ...       ...
120   -0.070843 -0.029804     146        1  0.276806
68    -0.007987  0.012371     147        1  0.260550
126   -0.149984 -0.072677     148        1  0.259649
31    -0.079648 -0.041968     149        1  0.242028
27    -0.161116  0.012263     150        1  0.200973

[150 rows x 5 columns], topic_info=        Term         Freq        Total  Category  logprob  loglift
333     seri  4004.000000  4004.000000   Default  30.0000  30.0000
492    music  5319.000000  5319.000000   Default  29.0000  29.0000
26    episod  3063.000000  3063.000000   Default  28.0000  28.0000
107   comedi  4181.000000  4181.000000   Default  27.0000  27.0000
131     play  9945.000000  9945.000000   Default  26.0000  26.0000
...      ...          ...          ...       ...      ...      ...
733     save    35.608746  1016.228271  Topic150  -4.8147   2.8585
1270    type    36.292328  1423.299438  Topic150  -4.7957   2.5406
617     walk    34.413326   986.345337  Topic150  -4.8489   2.8542
677     form    31.218309  1094.023193  Topic150  -4.9463   2.6531
1510   earli    30.479515  1875.960938  Topic150  -4.9702   2.0899

[8770 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
5450    127  0.957938   aamir
4769      7  0.018566   aaron
4769     11  0.083546   aaron
4769     24  0.157809   aaron
4769     77  0.491994   aaron
...     ...       ...     ...
2639     33  0.221826    zoom
2639     50  0.020166    zoom
2639     60  0.725976    zoom
7671    147  0.981771   zorro
4492     55  0.962093  zucker

[61776 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[112, 3, 113, 110, 59, 115, 78, 84, 118, 149, 26, 7, 87, 137, 130, 101, 146, 80, 109, 133, 50, 45, 93, 22, 135, 29, 63, 97, 134, 85, 75, 123, 148, 92, 43, 116, 114, 120, 119, 125, 1, 30, 90, 48, 34, 52, 5, 82, 15, 141, 70, 132, 96, 56, 2, 124, 150, 60, 44, 35, 99, 31, 37, 47, 74, 86, 17, 12, 9, 18, 24, 6, 105, 4, 13, 147, 39, 54, 68, 41, 122, 49, 65, 11, 89, 76, 16, 8, 62, 108, 91, 83, 129, 51, 14, 27, 117, 94, 55, 38, 25, 126, 142, 140, 102, 53, 10, 33, 73, 67, 21, 66, 71, 46, 61, 40, 57, 106, 36, 111, 95, 98, 79, 131, 23, 139, 42, 144, 64, 103, 136, 145, 88, 19, 77, 20, 72, 143, 58, 128, 104, 138, 100, 107, 81, 121, 69, 127, 32, 28])

In [15]:
# Visualize negative topic words
pyLDAvis.enable_notebook()
neg_vis = pyLDAvis.gensim.prepare(neg_lda_model, neg_bow_corpus, neg_dictionary)
neg_vis

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
70    -0.098949  0.184216       1        1  3.175932
89    -0.230657 -0.011539       2        1  3.033136
16    -0.207187 -0.018535       3        1  2.742292
118   -0.141652  0.019664       4        1  2.629073
65    -0.182004 -0.062679       5        1  2.106678
...         ...       ...     ...      ...       ...
107    0.026761 -0.001468     146        1  0.267320
21     0.021056 -0.080796     147        1  0.263918
101    0.037852  0.004327     148        1  0.257526
23     0.063934  0.013624     149        1  0.253645
92     0.125421 -0.036923     150        1  0.240281

[150 rows x 5 columns], topic_info=         Term          Freq         Total  Category  logprob  loglift
71     origin   4234.000000   4234.000000   Default  30.0000  30.0000
163    horror   4410.000000   4410.000000   Default  29.0000  29.0000
1491     book   3047.000000   3047.000000   Default  28.0000  28.0000
418    action   3537.000000   3537.000000   Default  27.0000  27.0000
128   charact  14963.000000  14963.000000   Default  26.0000  26.0000
...       ...           ...           ...       ...      ...      ...
1420    comic     85.697792   1002.647522  Topic150  -4.0510   3.5715
126   brother     66.942688   1290.385742  Topic150  -4.2980   3.0723
2061  portion     37.402981    127.024994  Topic150  -4.8801   4.8085
11      fight     45.658333   2236.948975  Topic150  -4.6806   2.1394
34       time     38.341763  15699.854492  Topic150  -4.8553   0.0163

[8701 rows x 6 columns], token_table=      Topic      Freq    Term
term                         
5660      6  0.025021   aaron
5660     26  0.125107   aaron
5660     34  0.150128   aaron
5660     73  0.588001   aaron
5660     74  0.100085   aaron
...     ...       ...     ...
993      91  0.588784    zoom
993     130  0.102397    zoom
7195     38  0.985280   zucco
7654     37  0.774187  zucker
7654    146  0.184330  zucker

[63559 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[71, 90, 17, 119, 66, 39, 138, 137, 143, 77, 46, 16, 26, 37, 41, 21, 18, 96, 34, 85, 98, 31, 80, 94, 84, 144, 29, 75, 149, 25, 60, 147, 49, 57, 87, 19, 23, 113, 12, 55, 99, 27, 107, 4, 28, 112, 58, 42, 81, 33, 51, 13, 40, 120, 126, 7, 68, 127, 114, 122, 30, 69, 32, 111, 3, 6, 106, 8, 65, 14, 91, 48, 88, 70, 117, 38, 95, 11, 104, 36, 67, 140, 128, 118, 5, 1, 9, 63, 142, 130, 52, 125, 150, 56, 76, 2, 116, 20, 74, 35, 148, 50, 103, 145, 121, 72, 82, 78, 89, 134, 62, 139, 44, 54, 61, 45, 10, 135, 124, 64, 43, 141, 100, 109, 83, 133, 86, 110, 47, 132, 115, 59, 53, 146, 136, 129, 123, 131, 97, 101, 79, 92, 73, 15, 105, 108, 22, 102, 24, 93])

In [16]:
def get_sentiment(text):
    count = 0
    pos_score = 0
    neg_score = 0
    #get what positive topics might be related
    bow_vector = pos_dictionary.doc2bow(preprocess(text))
    
    for idx, score in sorted(pos_lda_model[bow_vector], key=lambda tup:-1*tup[1]):
        count+=1
        pos_score += score
        if count > 2:
            break
    pos_score = pos_score/3
    pos_score *= 100
    
    count = 0
    #get what negative topics might be related
    bow_vector = neg_dictionary.doc2bow(preprocess(text))
    for idx, score in sorted(neg_lda_model[bow_vector], key=lambda tup:-1*tup[1]):    
        neg_score += score
        count+=1
        if count > 2:
            break
    neg_score = neg_score/3
    neg_score *= 100
    
    result = 0
    if pos_score>neg_score:
        result = (pos_score - neg_score)/(pos_score + neg_score)
        result *= 100
        result = 50 + (result*2)
        return result
    else:
        result = (neg_score - pos_score)/(pos_score + neg_score)
        result *= 100
        result = 50+(result*2)
        return result

In [17]:
def get_general_sentiment(text):
    count = 0
    pos_score = 0
    neg_score = 0
    #get what positive topics might be related
    bow_vector = pos_dictionary.doc2bow(preprocess(text))
    
    for idx, score in sorted(pos_lda_model[bow_vector], key=lambda tup:-1*tup[1]):
        count+=1
        pos_score += score
        if count > 2:
            break
    pos_score = pos_score/3
    pos_score *= 100
    
    count = 0
    #get what negative topics might be related
    bow_vector = neg_dictionary.doc2bow(preprocess(text))
    for idx, score in sorted(neg_lda_model[bow_vector], key=lambda tup:-1*tup[1]):    
        neg_score += score
        count+=1
        if count > 2:
            break
    neg_score = neg_score/3
    neg_score *= 100

    if pos_score>neg_score:
        return "positive"
    else:
        return "negative"

In [20]:
unseen_movie_description = input("Please enter a movie description to analyze: ")
result = round(get_sentiment(unseen_movie_description), 3)
print("\nWe predict that opinions on this movie are generally {}.".format(get_general_sentiment(unseen_movie_description)))
print("\nWe predict that this movie has a rating of ~{}%.".format(result))


We predict that opinions on this movie are generally negative.


ZeroDivisionError: float division by zero